In [12]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 5GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/sick-sentence-similarity/SICK.txt
/kaggle/input/glove6b50dtxt/glove.6B.50d.txt


In [ ]:
!pip install sentence-transformers

Here, I am gonna try out various methods to infer sentence similarities. The methods I am gonna try out are as follows:
1. Averaging Glove embeddings & finding cosine distance.
2. Using smooth inverse frequency on word embeddings.
3. Using Word Movers Distance method on embeddings.
4. Google Sentence Encoder
5. Cosine Similarity on BERT embeddings.

In [ ]:
import re
from nltk.corpus import stopwords
import seaborn as sns
import matplotlib.pyplot as plt
import scipy
from sklearn.preprocessing import MinMaxScaler
from sentence_transformers import SentenceTransformer
from sklearn.decomposition import TruncatedSVD

# Preparing the Data
The data I'll be using for practice is SICK data (https://zenodo.org/record/2787612) that contains 10,000 English sentence pairs labelled with their semantic relatedness and entailment relation

In [ ]:
original_df = pd.read_csv('../input/sick-sentence-similarity/SICK.txt', header = 0, error_bad_lines = False, sep = '\t')
display(original_df.head())
display(len(original_df))

In [ ]:
display(original_df.tail(10))

# 1. Averaging Glove Embeddings and Cosine Distance

In [ ]:
gloveFile = '../input/glove6b50dtxt/glove.6B.50d.txt'
def loadGloveModel(gloveFile):
    print ("Loading Glove Model")
    with open(gloveFile, encoding="utf8" ) as f:
        content = f.readlines()
    model = {}
    for line in content:
        splitLine = line.split()
        word = splitLine[0]
        embedding = np.array([float(val) for val in splitLine[1:]])
        model[word] = embedding
    print ("Done.",len(model)," words loaded!")
    return model

model = loadGloveModel(gloveFile)

In [ ]:
def preprocess(raw_text):
    # keep only words
    letters_only_text = re.sub("[^a-zA-Z]", " ", raw_text)

    # convert to lower case and split 
    words = letters_only_text.lower().split()

    # remove stopwords
    stopword_set = set(stopwords.words("english"))
    cleaned_words = list(set([w for w in words if w not in stopword_set]))
    
    # remove the words we do not have an embedding for
    preprocessed_words = list(set([w for w in cleaned_words if w in list(model.keys())]))

    return preprocessed_words

def cosine_distance_between_two_words(word1, word2):
    return (1- scipy.spatial.distance.cosine(model[word1], model[word2]))

def calculate_heat_matrix_for_two_sentences(s1,s2):
    s1 = preprocess(s1)
    s2 = preprocess(s2)
    result_list = [[cosine_distance_between_two_words(word1, word2) for word2 in s2] for word1 in s1]
    result_df = pd.DataFrame(result_list)
    result_df.columns = s2
    result_df.index = s1
    return result_df

def cosine_distance_on_sentences(s1, s2):
    vector_1 = np.mean([model[word] for word in preprocess(s1)],axis=0)
    vector_2 = np.mean([model[word] for word in preprocess(s2)],axis=0)
    cosine = scipy.spatial.distance.cosine(vector_1, vector_2)
    # print('Word Embedding method with a cosine distance asses that our two sentences are similar to',round((1-cosine)*100,2),'%')
    return cosine

def heat_map_matrix_between_two_sentences(s1,s2):
    df = calculate_heat_matrix_for_two_sentences(s1,s2)
    fig, ax = plt.subplots(figsize=(5,5)) 
    ax_blue = sns.heatmap(df, cmap="YlGnBu")
    # ax_red = sns.heatmap(df)
    print(cosine_distance_wordembedding_method(s1, s2))
    return ax_blue

def evaluate_cosine_distance_on_dataset(df):
    predicted_similarity = []
    cosine_distance = []
    for i in range(len(df)):
        #print(df.iloc[i, 1])
        #print(type(df.iloc[i, 1]))
        cosine_distance_between_sentences = cosine_distance_on_sentences(df.iloc[i,1], df.iloc[i, 2])
        cosine_distance.append(cosine_distance_between_sentences)
    scaler = MinMaxScaler()
    cosine_distance = np.array(cosine_distance)
    return cosine_distance
    

In [ ]:
# Now we test it on the given original_df dataset

cosine_distance = evaluate_cosine_distance_on_dataset(original_df)
print(cosine_distance)



In [ ]:
# Let's now rescale the distances so that they fit in the range of 1 to 5. 
scaler = MinMaxScaler()
cosine_distance_scaled = scaler.fit_transform((1-cosine_distance).reshape(-1, 1))
predicted_similarity = np.multiply(np.array(cosine_distance_scaled), 4) + 1     #rescaling the data into 1 to 5 range (just like the relatedness score)
print(predicted_similarity)
print(original_df['relatedness_score'])

In [ ]:
pred_similarity_df = pd.DataFrame(predicted_similarity)
display(pred_similarity_df.describe())

# Look at the goddamn mess, seems like either I did a terrible job at scaling or the model is producing bad results (and isn't as good as I thought it would be).

# Let's try to get the range of the actual relatedness score
display(original_df['relatedness_score'].describe())

In [ ]:
# Now we evaluate the results by calculating the MSE of the predicted similarity against, the actual similarity

# 2. Smooth Inverse Frequency

This approach was proposed by Sanjeev Arora et al. in their paper [A Simple but tough-to-beat baseline](https://openreview.net/pdf?id=SyK00v5xx) which solves several fundamental problems faced by the method used above. I will first list some of the problems, and then list some potential solutions, and then finally elaborate a bit upon the approach adopted by SIF.
The problem in averaging and distance technique used above is:
1. Non-weighted averaging of word-embeddings is arbitrary. That is, we know from texts that each word has different levels of impact on the text, and therefore a simple non-weighted averaging probably wouldn't provide an accurate representation of the sentence.
2. While stop words are removed in the approach above, but still there are several non-useful words left in the text, which cause the average of all the embeddings to adrift towards a meaningless (their, then, just) space in word embeddings. So essentially the problem is - Similarity model cannot identify the true meaning of the sentence because a large majority of it has no relevance to what the sentence is actually implying. 

These problems can be solved by several ways:
1. Training a supervised ML model (with extensively marked data) to enable the model to identify the specific things it should be looking out for - Happiness, assertiveness, etc.
2. An unsupervised approach (proposed in this paper) - Compute the principal component from a weighted average of words in multiple sentences. And then subtract from these embeddings their projections on their first principal component.

**SIF** does the task in the following ways:
1. **Weighted Average**: It takes the weighted average of the word embeddings in a sentence using the formulae -> [a/(a+p(w)] here, a is a hyperparameter (usually set at 0.001) and p(w) represents the frequency of the word in the sentence or document.
2. **Common Component Removal**: SIF computes the principal component of the resulting embeddings for a set of sentences. It then subtracts from these sentence embeddings their projections on their first principal component. This should remove variation related to frequency and syntax that is less relevant semantically.

Let's try it out!





In [ ]:
# This function would remove the principal component of the embeddings sent to it
def remove_first_principal_component(X):
    svd = TruncatedSVD(n_components=1, n_iter=7, random_state=0)
    svd.fit(X)
    pc = svd.components_
    XX = X - X.dot(pc.transpose()) * pc
    return XX

In [ ]:
def run_sif_benchmark(sentences1, sentences2, model, freqs={}, use_stoplist=False, a=0.001): 
    total_freq = sum(freqs.values())
    
    embeddings = []
    
    # SIF requires us to first collect all sentence embeddings and then perform 
    # common component analysis.
    for (sent1, sent2) in zip(sentences1, sentences2): 
        
        tokens1 = sent1.tokens_without_stop if use_stoplist else sent1.tokens
        tokens2 = sent2.tokens_without_stop if use_stoplist else sent2.tokens
        
        tokens1 = [token for token in tokens1 if token in model]
        tokens2 = [token for token in tokens2 if token in model]
        
        weights1 = [a/(a+freqs.get(token,0)/total_freq) for token in tokens1]
        weights2 = [a/(a+freqs.get(token,0)/total_freq) for token in tokens2]
        
        embedding1 = np.average([model[token] for token in tokens1], axis=0, weights=weights1)
        embedding2 = np.average([model[token] for token in tokens2], axis=0, weights=weights2)
        
        embeddings.append(embedding1)
        embeddings.append(embedding2)
        
    embeddings = remove_first_principal_component(np.array(embeddings))
    sims = [cosine_similarity(embeddings[idx*2].reshape(1, -1), 
                              embeddings[idx*2+1].reshape(1, -1))[0][0] 
            for idx in range(int(len(embeddings)/2))]

    return sims

# 5. BERT with Cosine Distance

In [19]:
def preprocess(raw_text):
    # keep only words
    letters_only_text = re.sub("[^a-zA-Z]", " ", raw_text)

    # convert to lower case and split 
    words = letters_only_text.lower().split()

    # remove stopwords
    stopword_set = set(stopwords.words("english"))
    cleaned_words = list(set([w for w in words if w not in stopword_set]))
    
    # remove the words we do not have an embedding for
    #preprocessed_words = list(set([w for w in cleaned_words if w in list(model_5.keys())]))
    preprocessed_words = cleaned_words

    return preprocessed_words

def bert_cosine_distance_on_sentences(s1, s2):
    sentence_list_1 = preprocess(s1)
    sentence_list_2 = preprocess(s2)
    sentence_1 = ''
    sentence_2 = ''
    for word in sentence_list_1:
        sentence_1 += word
        sentence_1 += ' '
    sentence_1 = sentence_1[:-1]
    for word in sentence_list_2:
        sentence_2 += word
        sentence_2 += ' '
    sentence_2 = sentence_2[:-1]
    vector_1 = model_5.encode(sentence_1)
    vector_2 = model_5.encode(sentence_2)
    cosine = scipy.spatial.distance.cosine(vector_1, vector_2)
    # print('Word Embedding method with a cosine distance asses that our two sentences are similar to',round((1-cosine)*100,2),'%')
    return cosine

def evaluate_bert_cosine_distance_on_dataset(df):
    predicted_similarity = []
    cosine_distance = []
    for i in range(len(df)):
        #print(df.iloc[i, 1])
        #print(type(df.iloc[i, 1]))
        cosine_distance_between_sentences = bert_cosine_distance_on_sentences(df.iloc[i,1], df.iloc[i, 2])
        cosine_distance.append(cosine_distance_between_sentences)
    #scaler = MinMaxScaler()
    cosine_distance = np.array(cosine_distance)
    return cosine_distance
    

In [ ]:
model_5 = SentenceTransformer('bert-base-nli-mean-tokens')

In [20]:
cosine_distance = evaluate_bert_cosine_distance_on_dataset(original_df)

# Let's now rescale the distances so that they fit in the range of 1 to 5. 
scaler = MinMaxScaler()
cosine_distance_scaled = scaler.fit_transform((1-cosine_distance).reshape(-1, 1))
predicted_similarity = np.multiply(np.array(cosine_distance_scaled), 4) + 1     #rescaling the data into 1 to 5 range (just like the relatedness score)
print(predicted_similarity)
print(original_df['relatedness_score'])

# WOah!!! Look at that, looks pretty good actually



[[4.65706752]
 [4.26739826]
 [4.76713737]
 ...
 [2.19195643]
 [2.3998801 ]
 [2.20057684]]
0       4.5
1       3.2
2       4.7
3       3.6
4       3.4
       ... 
9835    1.0
9836    1.0
9837    1.0
9838    1.2
9839    1.0
Name: relatedness_score, Length: 9840, dtype: float64
